In [1]:
# Import libraries
import math
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import sys

from numpy.polynomial import polynomial as P

In [2]:
# Times are in minutes
stations = [
    #Station Name,          East,   West
    ("Recto",               2.00,   7.00),
    ("Legarda",             2.75,   2.00),
    ("Pureza",              2.75,   2.75),
    ("V. Mapa",             2.50,   2.75),
    ("J. Ruiz",             1.75,   2.50),
    ("Gilmore",             2.25,   1.75),
    ("Betty-Go Belmonte",   2.25,   2.25),
    ("Araneta Cubao",       3.00,   2.25), 
    ("Anonas",              2.00,   3.00),
    ("Katipunan",           4.00,   2.00),
    ("Santolan",            3.50,   4.00),
    ("Marikina-Pasig",      4.50,   3.50),   
    ("Antipolo",            7.00,   4.50)
]

NSTATIONS = len(stations)



In [3]:
def read_data(filename):
    """Reads data from a file and returns a numpy array of the data"""
    data = pd.read_csv(filename, header=0)
    return data

monday_raw = read_data("Monday.csv")
monday_cum = monday_raw.cumsum()

monday_cum

Recto:Entry  Recto:Exit  Legarda:Entry  Legarda:Exit  Pureza:Entry  \
0          0.00        0.00           0.00          0.00          0.00   
1        139.75        0.00           8.75          0.00         27.25   
2        931.50     1339.50         108.75        570.50        243.50   
3       2498.25     4405.75         341.50       3330.50        802.00   
4       4480.50     8058.50         644.75       5537.25       1577.75   
5       6122.50    11700.75         869.50       7056.50       2058.25   
6       7721.25    14263.75        1410.00       8156.50       2388.50   
7       9274.50    16651.75        2151.50       9169.50       2757.25   
8      10972.50    18397.25        3032.75       9986.75       3188.25   
9      12705.00    20284.00        3965.75      11072.50       3706.50   
10     14504.75    22024.25        4830.00      11776.75       4263.25   
11     16513.75    23790.00        5712.50      12370.00       4837.75   
12     18956.50    25363.00        6946.25      12808.75       5545.25   
13     22107.25    27158.75        8331.50      13297.25       6289.75   
14     25892.75    29205.25       10074.00      13776.25       7018.25   
15     29151.25    31068.00       11526.25      14283.25       7560.00   
16     31314.00    32364.25       12519.25      14650.50       7923.75   
17     32616.25    33204.25       13102.00      14918.00       8187.75   
18     32958.50    33450.75       13307.25      15002.25       8243.50   
19     32958.50    33450.75       13307.25      15002.25       8243.50   
20     32958.50    33450.75       13307.25      15002.25       8243.50   

    Pureza:Exit  V. Mapa:Entry  V. Mapa:Exit  J. Ruiz:Entry  J. Ruiz:Exit  \
0          0.00           0.00          0.00           0.00          0.00   
1          0.00          22.50          0.00           6.75          0.00   
2        227.75         226.25        167.75          87.75         95.50   
3        778.75         881.50        526.75         390.00        335.00   
4       1448.25        1667.50       1150.25         669.50        773.00   
5       2238.00        2163.50       1784.00         863.75       1204.25   
6       2944.00        2498.25       2291.25        1005.50       1396.25   
7       3648.50        2811.25       2748.25        1108.00       1531.50   
8       4177.50        3137.00       3196.50        1216.75       1642.25   
9       4676.75        3548.50       3620.75        1320.75       1739.75   
10      5184.75        3969.75       4034.50        1434.00       1841.25   
11      5566.50        4431.00       4419.25        1557.50       1949.50   
12      5943.50        4987.25       4863.00        1728.75       2062.50   
13      6376.00        5672.00       5394.75        1947.00       2213.50   
14      7015.50        6533.25       6180.25        2315.00       2432.00   
15      7732.75        7278.50       6980.50        2600.25       2655.00   
16      8231.00        7760.00       7521.50        2726.50       2817.00   
17      8553.50        8118.50       7887.25        2794.50       2917.00   
18      8649.00        8266.25       7978.25        2809.00       2944.75   
19      8649.00        8266.25       7978.25        2809.00       2944.75   
20      8649.00        8266.25       7978.25        2809.00       2944.75   

    ...  Anonas:Entry  Anonas:Exit  Katipunan:Entry  Katipunan:Exit  \
0   ...          0.00         0.00             0.00            0.00   
1   ...         28.25         0.00            81.00            0.00   
2   ...        409.00       212.75           807.75          145.00   
3   ...       1180.50      1371.25          1697.50          780.75   
4   ...       1983.50      3154.75          2705.00         1598.75   
5   ...       2601.25      4378.75          3742.50         2268.25   
6   ...       3110.50      5136.50          4515.50         2726.25   
7   ...       3655.25      5732.00          5102.00         3094.25   
8   ...       4221.50      6233.50       

In [4]:
train_0_count = []
train_0_time = []

class Station():
    def __init__(self, name, entry_coeffs, exit_coeffs, idx, east_time, west_time):
        self.name = name
        # entry and exit in hours
        self.entry = P.Polynomial(entry_coeffs)
        self.exit = P.Polynomial(exit_coeffs)
        self.idx = idx
        self.east_time = east_time
        self.west_time = west_time

        # next stations
        self.east_next = None
        self.west_next = None

        # number of passengers waiting
        self.east_bound = 0
        self.west_bound = 0

        # number of potentially exiting passengers
        self.east_exiting = 0
        self.west_exiting = 0

    def step(self, start, step_size):
        # entering passengers
        entering = max(0, self.entry(start + step_size) - self.entry(start))
        # entering = self.entry(start + step_size) - self.entry(start)

        self.east_bound += entering * (12 - self.idx) / 12
        self.west_bound += entering * self.idx / 12
        
        # potentially exiting passengers
        exiting = max(0, self.exit(start + step_size) - self.exit(start))
        # exiting = self.exit(start + step_size) - self.exit(start)

        self.east_exiting += exiting * self.idx / 12
        self.west_exiting += exiting * (12 - self.idx) / 12

        print(self.name.ljust(20, ' '), end='')
        print(", ".join([str(round(x, 2)).ljust(5, ' ') for x in [entering, exiting, self.east_bound, self.west_bound, self.east_exiting, self.west_exiting]]))
    
    def __str__(self):
        return self.name


class Train():
    def __init__(self, capacity, name, start_station, east, time_to_active):
        self.capacity = capacity
        self.name = name

        self.passengers = 0
        self.time_left = time_to_active
        self.east = east
        self.next_station = start_station

        print("Train", self.name, "will start at", self.next_station.name, "in", round(self.time_left * 60, 2), "minutes")
    
    def step(self, time, step_size):        
        self.time_left -= step_size

        print("Train", self.name, "en route to", self.next_station.name, "with", round(self.time_left * 60, 2), "minutes left")
        if self.time_left <= 0.0001:
            curr_station = self.next_station

            print("\nTrain", self.name, "arrived at", curr_station.name)
            Global.load_unload_passengers(time, self, curr_station, self.east)
            
            if self.east:
                # reverse if terminal station
                if curr_station == curr_station.east_next:
                    self.east = False
            else:
                if curr_station == curr_station.west_next:
                    self.east = True
        
            if self.name == 1:
                train_0_time.append(time)
                train_0_count.append(self.passengers)


class Global():
    def __init__(self, step_size, stations, trains):
        self.step_size = step_size
        self.stations = stations
        self.trains = trains
        self.time = 0

    def step(self):
        print("\nTime: ", round(self.time * 60, 2), "minutes")

        for station in self.stations:
            station.step(self.time, self.step_size)
        
        for train in self.trains:
            train.step(self.time, self.step_size)
        
        self.time += self.step_size
    
    @staticmethod
    def load_unload_passengers(time, train, station, east):
        if east:
            # Unload passengers
            exiting_passengers = max(0, math.floor(station.east_exiting))
            exiting_passengers = min(exiting_passengers, train.passengers)

            print("Unloading", exiting_passengers, "passengers")
            train.passengers -= exiting_passengers
            station.east_exiting -= exiting_passengers

            # load passengers
            loading_passengers = max(0, math.floor(station.east_bound))

            print("Loading", loading_passengers, "passengers")
            train.passengers += loading_passengers
            station.east_bound -= loading_passengers

            print("Train", train.name, "has", train.passengers, "passengers")

            train.time_left = station.east_time
            train.next_station = station.east_next
            print("Next station", train.next_station, "Ang susunod na istasyon ay", train.next_station)
            print("Ang oras na natitira ay", round(train.time_left * 60, 2))
        else:
            # Unload passengers
            exiting_passengers = max(0, math.floor(station.west_exiting))
            exiting_passengers = min(exiting_passengers, train.passengers)

            print("Unloading", exiting_passengers, "passengers")
            train.passengers -= exiting_passengers
            station.west_exiting -= exiting_passengers

            # load passengers
            loading_passengers = max(0, math.floor(station.west_bound))

            print("Loading", loading_passengers, "passengers")
            train.passengers += loading_passengers
            station.west_bound -= loading_passengers

            print("Train", train.name, "has", train.passengers, "passengers")

            train.time_left = station.west_time
            train.next_station = station.west_next
            print("Next station", train.next_station, "Ang susunod na istasyon ay", train.next_station)
            print("Ang oras na natitira ay", round(train.time_left * 60, 2))


In [5]:
interpolated = {}

for name, series in monday_cum.items():
    x = monday_cum.index.values
    y = series.values

    poly = P.polyfit(x, y, 9)

    interpolated[name] = poly

print(interpolated)

interpolated_df = pd.DataFrame(list(interpolated.items()), columns=['Name', 'Coefficients'])

interpolated_df

# P.Polynomial(interpolated_df[interpolated_df['Name'] == 'Recto:Entry']['Coefficients'].values[0])

{'Recto:Entry': array([ 3.76619904e+01, -1.38871597e+03,  1.91284764e+03, -7.46628227e+02,
        1.81851737e+02, -2.69159929e+01,  2.37670748e+00, -1.21101365e-01,
        3.27069587e-03, -3.61832894e-05]), 'Recto:Exit': array([ 2.34922063e+01, -5.96127523e+02,  4.60452472e+01,  5.94262398e+02,
       -1.93267430e+02,  2.82228255e+01, -2.28796748e+00,  1.06954445e-01,
       -2.71209279e-03,  2.89851751e-05]), 'Legarda:Entry': array([ 1.79174246e+01, -8.90720187e+02,  1.32941516e+03, -6.89315177e+02,
        1.80981968e+02, -2.63000223e+01,  2.22294857e+00, -1.08588891e-01,
        2.83848227e-03, -3.07094798e-05]), 'Legarda:Exit': array([ 5.83204350e+01, -1.40072324e+03,  1.05883772e+03,  6.22355093e+01,
       -8.83130100e+01,  1.79624607e+01, -1.76868815e+00,  9.48527114e-02,
       -2.66086118e-03,  3.06140464e-05]), 'Pureza:Entry': array([ 1.15110599e+01, -1.70947015e+02,  6.81428795e+01,  1.01266482e+02,
       -3.90374871e+01,  6.20519682e+00, -5.25450447e-01,  2.49639636e-02,

Name                                       Coefficients
0               Recto:Entry  [37.66199041605594, -1388.7159714373345, 1912....
1                Recto:Exit  [23.492206290112023, -596.1275226887765, 46.04...
2             Legarda:Entry  [17.917424606707883, -890.7201871491552, 1329....
3              Legarda:Exit  [58.320435031887115, -1400.723236635462, 1058....
4              Pureza:Entry  [11.511059948761737, -170.94701538916073, 68.1...
5               Pureza:Exit  [6.181530662477558, -236.51047377579835, 234.5...
6             V. Mapa:Entry  [16.34586516376783, -321.79295057901743, 250.1...
7              V. Mapa:Exit  [7.026762808519106, -145.32564261894865, 105.9...
8             J. Ruiz:Entry  [8.527908662986334, -248.3964930830865, 277.32...
9              J. Ruiz:Exit  [2.1467956530349834, 121.06709028021353, -285....
10            Gilmore:Entry  [12.601009011681471, -478.2156736192867, 668.5...
11             Gilmore:Exit  [2.26283168475618, 268.1233552313293, -558.613...
12  Betty-Go Belmonte:Entry  [7.134397085509991, -212.03789697138612, 244.3...
13   Betty-Go Belmonte:Exit  [1.515140051756094, 140.17669593454718, -293.8...
14      Araneta Cubao:Entry  [35.21079103027253, -1055.013420215174, 1239.4...
15       Araneta Cubao:Exit  [34.23778111763535, -682.1849918894109, 246.16...
16             Anonas:Entry  [21.995599811347486, -897.164640846149, 1168.5...
17              Anonas:Exit  [26.324586527582273, 36.69493030695387, -628.7...
18          Katipunan:Entry  [4.775864444580132, -559.0868025822468, 835.33...
19           Katipunan:Exit  [12.909435762436305, -101.24060913550265, -114...
20           Santolan:Entry  [11.835099120287715, -373.31071312727624, 393....
21            Santolan:Exit  [8.625586014435207, -340.59632309510687, 434.9...
22     Marikina-Pasig:Entry  [27.1712489063469, -1374.7420307752225, 1587.2...
23      Marikina-Pasig:Exit  [24.102145347031808, -838.6669368449539, 1121....
24           Antipolo:Entry  [56.092446643248, -2639.6002246189714, 3090.66...
25            Antipolo:Exit  [24.484299509496704, -817.2712244913704, 1094....

In [6]:
station_objs = []
train_objs = []

NTRAINS = 10
HEADWAY = round(2 * sum([x[1] for x in stations]) / NTRAINS * 4) / 4

print(HEADWAY)

for station in stations:
    entry_poly = interpolated_df[interpolated_df['Name'] == station[0] + ':Entry']['Coefficients'].values[0]
    exit_poly = interpolated_df[interpolated_df['Name'] == station[0] + ':Exit']['Coefficients'].values[0]

    station_instance = Station(station[0], entry_poly, exit_poly, stations.index(station), station[1] / 60, station[2] / 60)

    station_objs.append(station_instance)

station_objs[0].west_next = station_objs[0]
station_objs[-1].east_next = station_objs[-1]

for i in range(len(station_objs) - 1):
    station_objs[i].east_next = station_objs[i + 1]
    station_objs[i + 1].west_next = station_objs[i]

for i in range(NTRAINS // 2):
    train_objs.append(Train(1000, i, station_objs[0], True, ((i + 1) * HEADWAY + 0.25) / 60))
    train_objs.append(Train(1000, i + NTRAINS // 2, station_objs[-1], False, ((i + 1) * HEADWAY + 0.25) / 60))

print(station_objs[0].west_next)

global_state = Global(0.25/60, station_objs, train_objs)

for i in range(20 * 60 * 4):
    global_state.step()



train_0_series = pd.Series(train_0_count)
train_0_timeseries = pd.Series(train_0_time)

interpolated_train_poly = P.polyfit(train_0_time, train_0_count, 9)

P.Polynomial(interpolated_train_poly)

8.0
Train 0 will start at Recto in 8.25 minutes
Train 5 will start at Antipolo in 8.25 minutes
Train 1 will start at Recto in 16.25 minutes
Train 6 will start at Antipolo in 16.25 minutes
Train 2 will start at Recto in 24.25 minutes
Train 7 will start at Antipolo in 24.25 minutes
Train 3 will start at Recto in 32.25 minutes
Train 8 will start at Antipolo in 32.25 minutes
Train 4 will start at Recto in 40.25 minutes
Train 9 will start at Antipolo in 40.25 minutes
Recto

Time:  0 minutes
Recto               0    , 0    , 0.0  , 0.0  , 0.0  , 0.0  
Legarda             0    , 0    , 0.0  , 0.0  , 0.0  , 0.0  
Pureza              0    , 0    , 0.0  , 0.0  , 0.0  , 0.0  
V. Mapa             0    , 0    , 0.0  , 0.0  , 0.0  , 0.0  
J. Ruiz             0    , 0.5  , 0.0  , 0.0  , 0.17 , 0.33 
Gilmore             0    , 1.11 , 0.0  , 0.0  , 0.46 , 0.65 
Betty-Go Belmonte   0    , 0.58 , 0.0  , 0.0  , 0.29 , 0.29 
Araneta Cubao       0    , 0    , 0.0  , 0.0  , 0.0  , 0.0  
Anonas              0

Polynomial([ 8.48315613e+01, -4.47482744e+02,  8.29970222e+02, -3.85055447e+02,
        8.75512842e+01, -1.14996973e+01,  9.15517028e-01, -4.35193497e-02,
        1.13352595e-03, -1.24186816e-05], domain=[-1,  1], window=[-1,  1], symbol='x')

# TODO
- Figure out how to change NTRAINS dynamically and adjust spacing between trains
- Figure out how to handle initially odd NTRAINS
- Train and station capacity computations